In [ ]:
import os
os.environ['PYTHONHASHSEED'] = '0'
import random as rn
rn.seed(12345)
from numpy.random import seed
seed(42)
from tensorflow.compat.v1 import set_random_seed
set_random_seed(42)

import nibabel as nib
import nipy as ni
import numpy as np
import datetime
import shutil
import yaml
import csv
import json
import warnings
import time

from hashlib import md5
from scipy.interpolate import RegularGridInterpolator

warnings.filterwarnings('ignore')

In [39]:
def create_samples(config):
    """"""
    if config["block_size"] % 2 == 0:
        raise ValueError("block_size must be an odd number (1, 3, 5,...)")
    
    if config["reverse_samples"] and config["max_n_samples"] % 2 != 0:
        raise ValueError("max_n_samples can not be an odd number for reverse_samples == True.")
        
    subject_dir = os.path.join("../subjects", config["subject"])
    
    trk_path = os.path.join(subject_dir, config["trk_path"])
    dwi_path = os.path.join(subject_dir, config["dwi_path"])
    
    hasher = md5()
    for v in config.values():
        hasher.update(str(v).encode())
    
    save_dir = os.path.join(subject_dir, "samples", hasher.hexdigest())
    if os.path.exists(save_dir):
        print("Samples with this config have been created already:\n{}".format(save_dir))
        return None, None
    
    tracts = nib.streamlines.load(trk_path).tractogram # fiber coordinates in rasmm
    assert tracts.data_per_point is not None
    assert "t" in tracts.data_per_point
    
    dwi_img = nib.load(dwi_path)
    dwi_img = nib.funcs.as_closest_canonical(dwi_img)
    
    inv_affine = np.linalg.inv(dwi_img.affine)
    xyz2ijk = lambda r: inv_affine.dot([r[0], r[1], r[2], 1])[:3]
    
    dwi = dwi_img.get_data()


    n_fibers = len(tracts)
    fiber_lengths = [len(f) for f in tracts]
    n_samples = np.sum(fiber_lengths) - 2 * n_fibers
    if config["reverse_samples"]:
        n_samples *= 2 
    n_samples = min(n_samples, config["max_n_samples"])
    print(f'number of samples: {n_samples}')
    
    np.random.seed(42)
    perm = np.random.permutation(len(tracts))
    tracts = tracts[perm]
    
    inputs = []
    outputs = []
    total_samples = 0
    done=False
    for fi, f in enumerate(tracts):
        start = time.time()
        fib_len = len(f)-2
        split_num = fib_len // config['seq_len']
        skip_num = fib_len % config['seq_len']
        
        split_num = split_num * 2 if config["reverse_samples"] else split_num
        skip_num = skip_num * 2 if config["reverse_samples"] else skip_num
#         n_samples = n_samples - skip_num
        
        max_samples = split_num // 2 if config["reverse_samples"] else split_num
        tract_input = np.zeros((split_num, config['seq_len'], config['input_size']))
        tract_output = np.zeros((split_num, config['seq_len'], config['output_size']))
        for i, r in enumerate(f.streamline[1:-1]): # Exclude end points        
            try:
                idx = xyz2ijk(r) # anchor idx
                IDX = np.round(idx).astype(int)
                
                values = np.zeros([3, 3, 3,
                                   config["block_size"], config["block_size"], config["block_size"],
                                   dwi.shape[-1]])
                
                for x in range(config["block_size"]):
                    for y in range(config["block_size"]):
                        for z in range(config["block_size"]):
                            values[x, y, z,:] = dwi[
                                IDX[0] + x - 2 * (config["block_size"] // 2) : IDX[0] + x + 1,
                                IDX[1] + y - 2 * (config["block_size"] // 2) : IDX[1] + y + 1,
                                IDX[2] + z - 2 * (config["block_size"] // 2) : IDX[2] + z + 1,
                                :]
                fn = RegularGridInterpolator(([-1,0,1],[-1,0,1],[-1,0,1]), values)
                
                d = fn([idx[0]-IDX[0], idx[1]-IDX[1], idx[2]-IDX[2]])[0]
                d = d.flatten() # to get back the spatial order: reshape(bs, bs, bs, dwi.shape[-1])
                
            except IndexError:
                n_samples -= (2 if config["reverse_samples"] else 1)
                print("Index error at r={}, idx={}, fiber_idx={}\n".format(r,idx,perm[fi]) +
                      "Maybe wrong reference frame, or resampling failed."
                     )
                continue
                
            vout = f.data_for_points["t"][i+1].astype("float32")
            vin = f.data_for_points["t"][i].astype("float32")

            i_pos = i // config['seq_len']
            j_pos = i % config['seq_len']
            
            if (i_pos == max_samples):
                break
            tract_input[i_pos, j_pos,...] = np.hstack([vin, d]).astype("float32")
            tract_output[i_pos, j_pos ,...] = vout
            total_samples = total_samples + 1

            if config["reverse_samples"]:
                i_pos = (split_num // 2) + (i // config['seq_len'])
                j_pos = i % config['seq_len']
                
                tract_input[i_pos, j_pos,...] = np.hstack([-vout, d]).astype("float32")
                tract_output[i_pos, j_pos ,...] = -vin
                total_samples = total_samples + 1
      
            if total_samples >= n_samples:
                done = True
                break
                
        
        inputs.append(tract_input)
        outputs.append(tract_output)
        print("Finished {:3.0f}% in {}".format(100*total_samples/n_samples, time.time() - start), end="\r")
        
        if done:
            break         

    os.makedirs(save_dir)

    inputs = np.concatenate(inputs, axis=0)
    outputs = np.concatenate(outputs, axis=0)
    save_path = os.path.join(save_dir, "samples.npz")
    
    print("Saving {}".format(save_path))
    np.savez_compressed(save_path, inputs=inputs, outputs=outputs)
    
    config["n_samples"] = int(n_samples)
    config_path = os.path.join(save_dir, "config" + ".yml")
    print("Saving {}".format(config_path))
    with open(config_path, "w") as file:
            yaml.dump(config, file, default_flow_style=False)
            
    return inputs, outputs

In [42]:
config = dict(
    subject="992774",
    sample_type="rnn",
    seq_len=3,
    input_size=408,
    output_size=3,
    dwi_path = "fod_norm.nii.gz",
    trk_path = "resampled_fibers/merged_w100_smooth=5_npts=auto.trk",
    block_size = 3,
    reverse_samples = True,
    max_n_samples = 1002,
)

In [43]:
inputs, outputs = create_samples(config)

number of samples: 1002
Saving ../subjects/992774/samples/6b0ba25f7d39764d5bcc229287a8435c/samples.npz
Saving ../subjects/992774/samples/6b0ba25f7d39764d5bcc229287a8435c/config.yml


In [44]:
inputs[~np.all(inputs == 0, axis=(1, 2))].shape

(334, 3, 408)

In [45]:
inputs.shape

(334, 3, 408)

In [46]:
subject_dir = os.path.join("../subjects", config["subject"])

trk_path = os.path.join(subject_dir, config["trk_path"])
dwi_path = os.path.join(subject_dir, config["dwi_path"])

hasher = md5()
for v in config.values():
    hasher.update(str(v).encode())

save_dir = os.path.join(subject_dir, "samples", hasher.hexdigest())

tracts = nib.streamlines.load(trk_path).tractogram # fiber coordinates in rasmm
assert tracts.data_per_point is not None
assert "t" in tracts.data_per_point

dwi_img = nib.load(dwi_path)
dwi_img = nib.funcs.as_closest_canonical(dwi_img)

inv_affine = np.linalg.inv(dwi_img.affine)
xyz2ijk = lambda r: inv_affine.dot([r[0], r[1], r[2], 1])[:3]

dwi = dwi_img.get_data()

if config["reverse_samples"] and config["max_n_samples"] % 2 != 0:
    raise ValueError("max_n_samples can not be an odd number for reverse_samples == True.")

n_fibers = len(tracts)
fiber_lengths = [len(f) for f in tracts]
n_samples = np.sum(fiber_lengths) - 2 * n_fibers
if config["reverse_samples"]:
    n_samples *= 2 
n_samples = min(n_samples, config["max_n_samples"])
print(f'number of samples: {n_samples}')

np.random.seed(42)
perm = np.random.permutation(len(tracts))
tracts = tracts[perm]

number of samples: 1002


In [ ]:
config["reverse_samples"]

In [30]:
for fi, f in enumerate(tracts):
    start = time.time()
    fib_len = len(f)-2
    split_num = fib_len // config['seq_len']
    skip_num = fib_len % config['seq_len']

    split_num = split_num * 2 if config["reverse_samples"] else split_num
    skip_num = skip_num * 2 if config["reverse_samples"] else skip_num
    n_samples = n_samples - skip_num

    max_samples = split_num // 2 if config["reverse_samples"] else split_num
    print("###")
    print(split_num)
    print(skip_num)
    print(n_samples)

###
34
0
1000
###
26
4
996
###
26
4
992
###
26
2
990
###
20
4
986
###
32
4
982
###
22
4
978
###
32
0
978
###
18
2
976
###
18
2
974
###
18
4
970
###
26
4
966
###
18
2
964
###
18
2
962
###
24
4
958
###
20
0
958
###
22
4
954
###
20
4
950
###
30
2
948
###
18
4
944
###
24
0
944
###
36
2
942
###
34
4
938
###
52
4
934
###
20
0
934
###
30
2
932
###
16
2
930
###
22
0
930
###
28
0
930
###
22
2
928
###
24
2
926
###
16
0
926
###
12
4
922
###
16
2
920
###
26
0
920
###
24
0
920
###
44
4
916
###
14
2
914
###
32
2
912
###
20
2
910
###
14
2
908
###
64
4
904
###
16
0
904
###
30
0
904
###
50
0
904
###
20
2
902
###
18
0
902
###
40
2
900
###
16
0
900
###
42
0
900
###
24
4
896
###
34
0
896
###
28
2
894
###
34
4
890
###
34
4
886
###
14
2
884
###
14
0
884
###
36
4
880
###
18
4
876
###
38
2
874
###
34
0
874
###
44
0
874
###
32
0
874
###
14
4
870
###
24
2
868
###
32
4
864
###
22
2
862
###
52
4
858
###
34
2
856
###
40
2
854
###
38
0
854
###
32
2
852
###
18
0
852
###
16
0
852
###
18
2
850
###
38
0
850
###
22
4
84

-574
###
30
2
-576
###
22
0
-576
###
36
2
-578
###
38
0
-578
###
10
4
-582
###
18
2
-584
###
22
0
-584
###
24
2
-586
###
18
0
-586
###
28
0
-586
###
12
2
-588
###
16
0
-588
###
18
0
-588
###
24
2
-590
###
36
0
-590
###
22
2
-592
###
20
2
-594
###
38
2
-596
###
46
0
-596
###
14
4
-600
###
22
2
-602
###
38
4
-606
###
14
2
-608
###
32
0
-608
###
28
0
-608
###
34
4
-612
###
44
0
-612
###
26
4
-616
###
24
0
-616
###
18
2
-618
###
30
2
-620
###
24
0
-620
###
18
0
-620
###
22
2
-622
###
22
2
-624
###
18
0
-624
###
32
2
-626
###
18
0
-626
###
20
0
-626
###
34
2
-628
###
22
2
-630
###
18
4
-634
###
32
2
-636
###
24
2
-638
###
20
2
-640
###
34
4
-644
###
34
2
-646
###
38
2
-648
###
18
4
-652
###
26
0
-652
###
34
2
-654
###
48
4
-658
###
40
0
-658
###
26
0
-658
###
20
2
-660
###
38
0
-660
###
32
4
-664
###
28
4
-668
###
28
4
-672
###
56
2
-674
###
28
0
-674
###
22
4
-678
###
42
0
-678
###
18
4
-682
###
24
4
-686
###
18
2
-688
###
18
2
-690
###
26
0
-690
###
20
0
-690
###
22
2
-692
###
34
2
-694
#

4
-2084
###
20
2
-2086
###
20
0
-2086
###
26
4
-2090
###
20
4
-2094
###
26
0
-2094
###
24
2
-2096
###
26
4
-2100
###
16
0
-2100
###
46
4
-2104
###
20
4
-2108
###
16
0
-2108
###
54
2
-2110
###
26
2
-2112
###
30
4
-2116
###
14
4
-2120
###
22
2
-2122
###
18
2
-2124
###
22
2
-2126
###
38
0
-2126
###
40
0
-2126
###
38
2
-2128
###
48
0
-2128
###
16
0
-2128
###
14
4
-2132
###
24
4
-2136
###
26
4
-2140
###
20
4
-2144
###
16
4
-2148
###
34
4
-2152
###
30
0
-2152
###
30
0
-2152
###
32
0
-2152
###
28
4
-2156
###
22
2
-2158
###
50
4
-2162
###
24
0
-2162
###
40
4
-2166
###
26
0
-2166
###
20
0
-2166
###
20
0
-2166
###
26
2
-2168
###
26
0
-2168
###
20
0
-2168
###
16
4
-2172
###
22
0
-2172
###
42
4
-2176
###
28
0
-2176
###
30
4
-2180
###
20
4
-2184
###
26
4
-2188
###
24
0
-2188
###
16
4
-2192
###
32
0
-2192
###
46
0
-2192
###
20
0
-2192
###
16
0
-2192
###
24
0
-2192
###
32
0
-2192
###
18
4
-2196
###
18
2
-2198
###
12
4
-2202
###
12
4
-2206
###
18
2
-2208
###
42
4
-2212
###
16
0
-2212
###
22
0
-2212
##

22
2
-3572
###
40
2
-3574
###
22
2
-3576
###
22
0
-3576
###
48
4
-3580
###
28
0
-3580
###
18
4
-3584
###
20
4
-3588
###
28
2
-3590
###
34
2
-3592
###
14
2
-3594
###
18
2
-3596
###
22
2
-3598
###
20
4
-3602
###
28
0
-3602
###
28
4
-3606
###
30
4
-3610
###
28
2
-3612
###
34
4
-3616
###
36
0
-3616
###
28
2
-3618
###
14
4
-3622
###
28
2
-3624
###
20
4
-3628
###
16
2
-3630
###
14
0
-3630
###
16
4
-3634
###
46
4
-3638
###
30
0
-3638
###
20
0
-3638
###
40
2
-3640
###
22
0
-3640
###
16
4
-3644
###
24
0
-3644
###
14
0
-3644
###
40
4
-3648
###
32
2
-3650
###
16
2
-3652
###
28
2
-3654
###
42
4
-3658
###
20
2
-3660
###
44
0
-3660
###
22
2
-3662
###
20
2
-3664
###
26
2
-3666
###
18
2
-3668
###
26
2
-3670
###
32
4
-3674
###
18
2
-3676
###
14
2
-3678
###
38
2
-3680
###
32
4
-3684
###
24
2
-3686
###
52
0
-3686
###
20
2
-3688
###
16
0
-3688
###
22
2
-3690
###
30
2
-3692
###
20
2
-3694
###
20
0
-3694
###
48
0
-3694
###
20
4
-3698
###
16
0
-3698
###
22
2
-3700
###
18
2
-3702
###
26
0
-3702
###
36
0
-3702

###
40
0
-5078
###
32
2
-5080
###
40
0
-5080
###
16
0
-5080
###
18
0
-5080
###
38
4
-5084
###
24
0
-5084
###
20
4
-5088
###
38
0
-5088
###
20
2
-5090
###
46
4
-5094
###
14
2
-5096
###
32
2
-5098
###
24
0
-5098
###
28
0
-5098
###
32
4
-5102
###
14
0
-5102
###
30
0
-5102
###
30
0
-5102
###
20
4
-5106
###
36
4
-5110
###
30
0
-5110
###
24
0
-5110
###
28
4
-5114
###
22
2
-5116
###
10
4
-5120
###
20
0
-5120
###
36
0
-5120
###
20
0
-5120
###
26
2
-5122
###
28
0
-5122
###
26
4
-5126
###
32
0
-5126
###
44
4
-5130
###
38
2
-5132
###
24
0
-5132
###
20
2
-5134
###
26
0
-5134
###
58
0
-5134
###
20
0
-5134
###
20
4
-5138
###
26
4
-5142
###
24
2
-5144
###
30
4
-5148
###
14
2
-5150
###
22
0
-5150
###
28
2
-5152
###
26
4
-5156
###
24
4
-5160
###
28
4
-5164
###
18
0
-5164
###
36
4
-5168
###
38
0
-5168
###
26
4
-5172
###
14
0
-5172
###
18
4
-5176
###
24
4
-5180
###
20
4
-5184
###
24
2
-5186
###
28
4
-5190
###
20
2
-5192
###
18
0
-5192
###
28
0
-5192
###
26
4
-5196
###
14
0
-5196
###
22
4
-5200
###
22
2
-

...

0
-253988
###
30
0
-253988
###
24
4
-253992
###
24
4
-253996
###
22
0
-253996
###
20
4
-254000
###
46
0
-254000
###
22
0
-254000
###
54
4
-254004
###
22
2
-254006
###
32
4
-254010
###
26
2
-254012
###
18
4
-254016
###
14
4
-254020
###
24
2
-254022
###
34
4
-254026
###
20
0
-254026
###
26
2
-254028
###
60
0
-254028
###
16
4
-254032
###
44
4
-254036
###
42
2
-254038
###
48
4
-254042
###
40
2
-254044
###
22
2
-254046
###
24
0
-254046
###
24
4
-254050
###
48
4
-254054
###
30
0
-254054
###
34
0
-254054
###
32
2
-254056
###
26
2
-254058
###
34
2
-254060
###
20
2
-254062
###
28
2
-254064
###
28
0
-254064
###
24
2
-254066
###
26
0
-254066
###
40
0
-254066
###
12
4
-254070
###
20
2
-254072
###
16
2
-254074
###
24
4
-254078
###
44
0
-254078
###
30
2
-254080
###
22
2
-254082
###
16
4
-254086
###
16
0
-254086
###
24
2
-254088
###
26
4
-254092
###
18
2
-254094
###
14
2
-254096
###
22
4
-254100
###
28
0
-254100
###
16
4
-254104
###
12
4
-254108
###
16
2
-254110
###
20
4
-254114
###
30
2
-254116
###


22
2
-255490
###
38
4
-255494
###
40
0
-255494
###
16
0
-255494
###
24
0
-255494
###
20
4
-255498
###
20
4
-255502
###
18
0
-255502
###
26
0
-255502
###
22
4
-255506
###
16
4
-255510
###
30
4
-255514
###
20
0
-255514
###
32
0
-255514
###
42
2
-255516
###
32
4
-255520
###
22
2
-255522
###
40
0
-255522
###
20
0
-255522
###
16
2
-255524
###
20
2
-255526
###
16
2
-255528
###
16
2
-255530
###
20
2
-255532
###
14
0
-255532
###
36
4
-255536
###
40
2
-255538
###
38
4
-255542
###
22
4
-255546
###
36
2
-255548
###
44
2
-255550
###
20
0
-255550
###
18
2
-255552
###
32
0
-255552
###
20
0
-255552
###
28
2
-255554
###
30
2
-255556
###
18
4
-255560
###
18
2
-255562
###
24
2
-255564
###
22
4
-255568
###
26
2
-255570
###
26
2
-255572
###
22
2
-255574
###
22
4
-255578
###
18
4
-255582
###
24
0
-255582
###
30
0
-255582
###
34
0
-255582
###
34
4
-255586
###
44
0
-255586
###
20
2
-255588
###
20
2
-255590
###
48
4
-255594
###
12
2
-255596
###
18
0
-255596
###
20
2
-255598
###
20
0
-255598
###
22
4
-255602
#

###
16
0
-256950
###
20
2
-256952
###
28
0
-256952
###
26
2
-256954
###
14
2
-256956
###
16
4
-256960
###
32
0
-256960
###
16
4
-256964
###
38
4
-256968
###
18
4
-256972
###
36
0
-256972
###
38
0
-256972
###
34
0
-256972
###
26
0
-256972
###
18
0
-256972
###
36
0
-256972
###
18
0
-256972
###
60
2
-256974
###
22
2
-256976
###
20
2
-256978
###
18
0
-256978
###
22
0
-256978
###
12
4
-256982
###
18
0
-256982
###
22
2
-256984
###
12
0
-256984
###
26
2
-256986
###
22
0
-256986
###
16
4
-256990
###
34
4
-256994
###
22
4
-256998
###
40
2
-257000
###
42
2
-257002
###
38
0
-257002
###
20
0
-257002
###
24
4
-257006
###
30
4
-257010
###
30
0
-257010
###
28
4
-257014
###
30
0
-257014
###
16
0
-257014
###
20
0
-257014
###
20
4
-257018
###
24
2
-257020
###
46
4
-257024
###
22
0
-257024
###
22
2
-257026
###
44
4
-257030
###
26
4
-257034
###
24
2
-257036
###
28
2
-257038
###
36
0
-257038
###
24
4
-257042
###
22
2
-257044
###
34
2
-257046
###
36
0
-257046
###
18
2
-257048
###
22
2
-257050
###
22
0
-2570

-258484
###
24
2
-258486
###
18
4
-258490
###
18
2
-258492
###
22
4
-258496
###
26
2
-258498
###
32
2
-258500
###
32
2
-258502
###
18
4
-258506
###
34
2
-258508
###
32
0
-258508
###
40
2
-258510
###
28
2
-258512
###
40
4
-258516
###
20
4
-258520
###
18
0
-258520
###
16
2
-258522
###
24
2
-258524
###
26
2
-258526
###
32
4
-258530
###
16
2
-258532
###
48
4
-258536
###
12
4
-258540
###
46
4
-258544
###
18
4
-258548
###
28
0
-258548
###
30
0
-258548
###
24
2
-258550
###
22
4
-258554
###
18
0
-258554
###
18
0
-258554
###
18
2
-258556
###
22
0
-258556
###
22
0
-258556
###
22
2
-258558
###
42
2
-258560
###
22
0
-258560
###
32
0
-258560
###
20
2
-258562
###
40
2
-258564
###
24
4
-258568
###
44
0
-258568
###
18
0
-258568
###
42
4
-258572
###
16
4
-258576
###
16
0
-258576
###
18
2
-258578
###
24
0
-258578
###
32
2
-258580
###
18
2
-258582
###
46
4
-258586
###
26
2
-258588
###
38
2
-258590
###
16
4
-258594
###
18
0
-258594
###
26
4
-258598
###
18
0
-258598
###
18
0
-258598
###
42
0
-258598
###
24

KeyboardInterrupt: 